In [1]:
import librosa
import numpy as np
from keras.layers import Dense
from keras.models import Sequential
from pydub import AudioSegment
from scipy import signal
from sklearn import preprocessing

In [2]:
pathAudio = '/home/stud/m/mh361/share/samples-stochastic/'
files = librosa.util.find_files(pathAudio, ext=['mp3'])

song_lounge_it = []
song_tuesday_night = []
song_kingtop = []
for file in files:
    if 'Maarten Schellekens - Lounge It' in file:
        song_lounge_it.append(file)
    if 'Maarten Schellekens - Tuesday Night Radio Edit' in file:
        song_tuesday_night.append(file)
    if 'Tea K Pea - kingtop' in file:
        song_kingtop.append(file)
song_lounge_it = sorted(song_lounge_it, key=lambda x: int(x.split('_')[-1].split('.')[0]))
song_tuesday_night = sorted(song_tuesday_night, key=lambda x: int(x.split('_')[-1].split('.')[0]))
song_kingtop = sorted(song_kingtop, key=lambda x: int(x.split('_')[-1].split('.')[0]))

In [3]:
full_songs = []
full_songs.extend(song_lounge_it)
full_songs.extend(song_tuesday_night)
full_songs.extend(song_kingtop)

In [4]:
def normalize_sample(sample):
    array_of_samples = sample.get_array_of_samples()
    np_arr = np.array(array_of_samples)
    np_arr = np_arr.reshape(1, -1)
    return preprocessing.normalize(np_arr)


samples = []
samples_sec_canal = []
for file_name in full_songs:
    sample = AudioSegment.from_mp3(file_name)
    mono_samples = sample.split_to_mono()
    normalized_sample = normalize_sample(mono_samples[0])[0]
    resampled_sample = signal.resample(normalized_sample, int(len(normalized_sample)/35))
    samples.append(resampled_sample)
    normalized_sample_sec_canal = normalize_sample(mono_samples[1])[0]
    resampled_sample_sec_canal = signal.resample(normalized_sample_sec_canal, int(len(normalized_sample)/35))
    samples_sec_canal.append(resampled_sample_sec_canal)

In [5]:
X_train = []
Y_train = []
for i in range(len(samples)-2):
    if i == 0:
        first_half = list(samples[i][-1500:])
    else:
        ref_samp = list(samples[i-1]) + list(samples[i])
        if len(ref_samp) < 1500:
            ref_samp_2 = list(samples[i-2]) + list(samples[i-1]) + list(samples[i])
            first_half = list(ref_samp_2[-1500:])
        else:
            first_half = list(ref_samp[-1500:])
    last_ref = list(samples[i+1]) + list(samples[i+2])
    last_half = list(last_ref[:500])
    X_train.append(first_half + last_half)
    Y_train.append(True)
    last_half = list(last_ref[500:1000])
    X_train.append(first_half + last_half)
    Y_train.append(True)

In [6]:
from numpy import random

def get_strange_end_part(samples, current_index, max_len):
    x = random.randint(max_len-1)
    if (x != current_index+1) and (x != current_index+2):
        ref_sample = list(samples[x]) + list(samples[x+1])
        return ref_sample[:500]
    else:
        return get_strange_end_part(samples, current_index, max_len)


for i in range(len(samples)-2):
    if i == 0:
        first_half = list(samples[i][-1500:])
    else:
        ref_samp = list(samples[i-1]) + list(samples[i])
        if len(ref_samp) < 1500:
            ref_samp_2 = list(samples[i-2]) + list(samples[i-1]) + list(samples[i])
            first_half = list(ref_samp_2[-1500:])
        else:
            first_half = list(ref_samp[-1500:])
    
    last_half = get_strange_end_part(samples, i, len(samples))
    X_train.append(first_half+last_half)
    Y_train.append(False)
    sec_last_half = get_strange_end_part(samples, i, len(samples))
    X_train.append(first_half+sec_last_half)
    Y_train.append(False)

In [7]:
X_train = np.array(X_train)
X_train = X_train.reshape(-1, 2000)
X_train.shape

(964, 2000)

In [8]:
Y_train = np.array(Y_train)
Y_train = Y_train.reshape(-1, 1)
Y_train.shape

(964, 1)

In [9]:
from keras.layers import Conv1D, LSTM, Flatten, CuDNNLSTM, MaxPool1D
from tensorflow.keras.optimizers import SGD

model = Sequential()
model.add(Conv1D(filters=1024, kernel_size=2, input_shape=(2000, 1))) # 2 # 3 / filters 512
model.add(MaxPool1D(pool_size=2, strides=2))
model.add(CuDNNLSTM(512, return_sequences=True)) # 256 # 8 #512 #256
model.add(Dense(256))
model.add(Flatten())
model.add(Dense(1, activation='sigmoid'))

model.compile(optimizer='rmsprop', loss='binary_crossentropy', metrics=['accuracy']) #1 'rmsprop' 2 'adam' 3 SGD(learning_rate=0.01)
model.summary()

2022-06-24 21:32:43.866869: I tensorflow/core/platform/cpu_feature_guard.cc:151] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  SSE4.1 SSE4.2 AVX AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2022-06-24 21:32:44.471142: I tensorflow/core/common_runtime/gpu/gpu_device.cc:1525] Created device /job:localhost/replica:0/task:0/device:GPU:0 with 9634 MB memory:  -> device: 0, name: GeForce RTX 2080 Ti, pci bus id: 0000:05:00.0, compute capability: 7.5


Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 conv1d (Conv1D)             (None, 1999, 1024)        3072      
                                                                 
 max_pooling1d (MaxPooling1D  (None, 999, 1024)        0         
 )                                                               
                                                                 
 cu_dnnlstm (CuDNNLSTM)      (None, 999, 512)          3149824   
                                                                 
 dense (Dense)               (None, 999, 256)          131328    
                                                                 
 flatten (Flatten)           (None, 255744)            0         
                                                                 
 dense_1 (Dense)             (None, 1)                 255745    
                                                        

In [10]:
model.fit(X_train, Y_train, epochs=350, batch_size=64)

Epoch 1/350


2022-06-24 21:32:46.579097: I tensorflow/stream_executor/cuda/cuda_dnn.cc:368] Loaded cuDNN version 7605
2022-06-24 21:32:46.581274: I tensorflow/core/platform/default/subprocess.cc:304] Start cannot spawn child process: No such file or directory
2022-06-24 21:32:46.582320: I tensorflow/core/platform/default/subprocess.cc:304] Start cannot spawn child process: No such file or directory
2022-06-24 21:32:46.582345: W tensorflow/stream_executor/gpu/asm_compiler.cc:80] Couldn't get ptxas version string: INTERNAL: Couldn't invoke ptxas --version
2022-06-24 21:32:46.582701: I tensorflow/core/platform/default/subprocess.cc:304] Start cannot spawn child process: No such file or directory
2022-06-24 21:32:46.582736: W tensorflow/stream_executor/gpu/redzone_allocator.cc:314] INTERNAL: Failed to launch ptxas
Relying on driver to perform ptx compilation. 
Modify $PATH to customize ptxas location.
This message will be only logged once.


16/16 [==============================] - 10s 372ms/step - loss: 3.0264 - accuracy: 0.4979
Epoch 2/350
16/16 [==============================] - 3s 181ms/step - loss: 0.7288 - accuracy: 0.4741
Epoch 3/350
16/16 [==============================] - 3s 183ms/step - loss: 0.7234 - accuracy: 0.4502
Epoch 4/350
16/16 [==============================] - 3s 185ms/step - loss: 0.7080 - accuracy: 0.5228
Epoch 5/350
16/16 [==============================] - 3s 184ms/step - loss: 1.9644 - accuracy: 0.4979
Epoch 6/350
16/16 [==============================] - 3s 184ms/step - loss: 0.6973 - accuracy: 0.4844
Epoch 7/350
16/16 [==============================] - 3s 189ms/step - loss: 0.6977 - accuracy: 0.4896
Epoch 8/350
16/16 [==============================] - 3s 191ms/step - loss: 1.0528 - accuracy: 0.5187
Epoch 9/350
16/16 [==============================] - 3s 192ms/step - loss: 0.6989 - accuracy: 0.5197
Epoch 10/350
16/16 [==============================] - 3s 192ms/step - loss: 0.6944 - accuracy: 0.5000


In [12]:
example_x_train = X_train[-5]
example_x_train = example_x_train.reshape(1, 2000)
model.predict(example_x_train) 

array([[0.44289085]], dtype=float32)

In [13]:
example_x_train = X_train[10]
example_x_train = example_x_train.reshape(1, 2000)
model.predict(example_x_train) 

array([[0.5155974]], dtype=float32)

In [22]:
from pathlib import Path

path_all_samples = '/home/stud/m/mh361/share/sample-pool/'
sample_files = librosa.util.find_files(path_all_samples, ext=['mp3'])
#random.shuffle(sample_files)
loaded_samples = {}
for file_path in sample_files:
    loaded_audio_file = AudioSegment.from_mp3(file_path)
    sample_array = loaded_audio_file.get_array_of_samples()
    resampled_part = signal.resample(sample_array, int(len(normalized_sample)/35))
    if len(resampled_part) >= 500:
        file_name = Path(file_path).stem
        loaded_samples[file_name] = resampled_part

In [23]:
list(loaded_samples.keys())[1273]

'Julia Felix - Sentience Council of Seers_55'

In [24]:
start_sample_name = list(loaded_samples.keys())[1273]
reference_sample = loaded_samples[start_sample_name]
reference_sample

array([ -8323.59377853, -14160.56406438, -15392.55525974, ...,
        -3779.99986771,  -4678.60430181,  -3563.38721555])

In [25]:
len(reference_sample)

17961

In [26]:
i = 0
max = 100
selected_samples = [start_sample_name]
song_counter = [start_sample_name, 0]
song_blacklist = []
older_reference_sample = None
while i < max:
    best_sample_name = None
    best_score = 0.00000
    best_sample = []
    for key, value in loaded_samples.items():
        if (key not in selected_samples) and (key[:-4] not in song_blacklist):
            if len(reference_sample) < 1500:
                ref_and_old_sample = list(older_reference_sample) + list(reference_sample)
                ref_and_next_sample = np.append(reference_sample[-1500:], value[:500])
            else:
                ref_and_next_sample = np.append(reference_sample[-1500:], value[:500])
            prediction = model.predict(ref_and_next_sample.reshape(1, 2000))
            score = prediction[0][0]
            if score > best_score:
                best_score = score
                best_sample_name = key
                best_sample = value
            if score > 0.99:
                break
        print('Predicted ' + best_sample_name + ' at position ' + str(i) + ' as best sample with score ' + str(
            best_score))
        older_reference_sample = reference_sample
        reference_sample = best_sample
        selected_samples.append(best_sample_name)
        if song_counter[0] in best_sample_name:
            song_counter[1] = song_counter[1]+1
        else:
            song_counter[0] = best_sample_name[:-4]
            song_counter[1] = 0
        if song_counter[1] >= 2:
            song_blacklist.append(best_sample_name[:-4])
        if len(song_blacklist) >= 3:
            song_blacklist = song_blacklist[1:]
        i += 1

Predicted Lobo Loco - Swinging Boss_171 at position 0 as best sample with score 1.0
Predicted the hermit - 05_FishiFish_9 at position 1 as best sample with score 1.0
Predicted Independent Music Licensing Collective - New Launch_37 at position 2 as best sample with score 0.9996948
Predicted Independent Music Licensing Collective - Schellekens_42 at position 3 as best sample with score 1.0
Predicted Independent Music Licensing Collective - Schellekens_69 at position 4 as best sample with score 0.99999
Predicted Independent Music Licensing Collective - New Launch_53 at position 5 as best sample with score 1.0
Predicted Makaih Beats - Dangerous_90 at position 6 as best sample with score 1.0
Predicted Holizna - Laundry On The Wire_54 at position 7 as best sample with score 1.0
Predicted Techtheist - Fakecore deconstruction_21 at position 8 as best sample with score 1.0
Predicted Maarten Schellekens - The Little Match Girl_16 at position 9 as best sample with score 1.0
Predicted Makaih Beats

In [20]:
new_song = AudioSegment.empty()
for sample in selected_samples:
    complete_path = '/home/stud/m/mh361/share/sample-pool/' + sample + '.mp3'
    loaded_sample = AudioSegment.from_mp3(complete_path)
    new_song += loaded_sample
new_song.export('/home/stud/m/mh361/share/music-out/' + 'karacho_3.mp3', format='mp3')

<_io.BufferedRandom name='/home/stud/m/mh361/share/music-out/karacho_3.mp3'>

In [21]:
new_song